# Implicit bias of GD for logistic regression on separable data

## Aim

The aim of this material is to code 
- gradient descent (GD)
- stochastic gradient descent (SGD)
- stochastic variance reduced gradient descent (SVRG)
for the logistic regression model, and to study their behaviour on separable data



# Table of content

[1. Introduction](#intro)<br>
[2. Models gradients and losses](#models)<br>
[3. Solvers](#solvers)<br>
[4. Comparison of all algorithms](#comparison)<br>

<a id='intro'></a>
# 1. Introduction

## 1.1. Preliminary





In [ ]:
import numpy as np
import matplotlib.pyplot as plt

%matplotlib inline

np.set_printoptions(precision=2)  # to have simpler print outputs with numpy

In [ ]:
from numpy.random import multivariate_normal
from scipy.linalg.special_matrices import toeplitz
from numpy.random import randn

def sigmoid(t):
    """Sigmoid function (overflow-proof)"""
    idx = t > 0
    out = np.empty(t.size)    
    out[idx] = 1 / (1. + np.exp(-t[idx]))
    exp_t = np.exp(t[~idx])
    out[~idx] = exp_t / (1. + exp_t)
    return out

def simu_logreg(w0, n_samples=1000, corr=0.5):
    """Simulation of a logistic regression model with Gaussian features
    and a Toeplitz covariance.
    
    Parameters
    ----------
    w0 : `numpy.array`, shape=(n_features,)
        Model weights
    
    n_samples : `int`, default=1000
        Number of samples to simulate
    
    corr : `float`, default=0.5
        Correlation of the features

    Returns
    -------
    X : `numpy.ndarray`, shape=(n_samples, n_features)
        Simulated features matrix. It contains samples of a centered 
        Gaussian vector with Toeplitz covariance.
    
    y : `numpy.array`, shape=(n_samples,)
        Simulated labels
    """
    n_features = w0.shape[0]
    cov = toeplitz(corr ** np.arange(0, n_features))
    X = multivariate_normal(np.zeros(n_features), cov, size=n_samples)
    p = sigmoid(X.dot(w0))
    y = np.random.binomial(1, p, size=n_samples)
    # Put the label in {-1, 1}
    y[:] = 2 * y - 1
    return X, y

<a id='models'></a>
# 2. Model gradients and losses

We want to minimize a goodness-of-fit function $F$, namely
$$
\arg\min_{w \in \mathbb R^d} \Big\{ F(w) \Big\}
$$
where $d$ is the number of features. 

In the case of the **logistic regression**, 
$$
F(w) = \frac 1n \sum_{i=1}^n f_i(w) = \frac{1}{n} \sum_{i=1}^n \log(1 + \exp(-y_i x_i^\top w)),
$$
where $n$ is the sample size, and where labels $y_i \in \{ -1, 1 \}$ for all $i$.

We need to be able to compute $F(w)$ and its gradient $\nabla F(w)$, in order to solve this problem, as well as $\nabla f_i(w)$ for stochastic gradient descent methods.




### QUESTIONS

<div class="alert alert-block alert-warning">
    <ol>
        <li>Compute (on paper) the gradient $\nabla f$, the gradient of $\nabla f_i$ for logistic regression.</li> </br>
         <li> Fill in the functions below for the computation of $f$, $\nabla f$, $\nabla f_i$ for logistic regression in the ModelLogReg class below (fill between the TODO and END TODO) </li>
    </ol>
</div>

In [ ]:
class ModelLogReg:
    """A class giving first order information for logistic regression
    
    Parameters
    ----------
    X : `numpy.array`, shape=(n_samples, n_features)
        The features matrix
    
    y : `numpy.array`, shape=(n_samples,)
        The vector of labels

    """    
    def __init__(self, X, y):
        self.X = X
        self.y = y
        self.n_samples, self.n_features = X.shape
    
    def loss(self, beta):
        """Computes f(w)"""
        y, X, n_samples = self.y, self.X, self.n_samples
        ### TODO
        
        ### END TODO
       
    def grad(self, beta):
        """Computes the gradient of f at w"""
        y, X, n_samples = self.y, self.X, self.n_samples
        ### TODO
        
        ### END TODO

    def grad_i(self, i, beta):
        """Computes the gradient of f_i at w"""
        x_i = self.X[i]
        ### TODO

        ### END TODO


    def lip(self):
        """Computes the Lipschitz constant of f"""
        X, n_samples = self.X, self.n_samples
        ### TODO
        
        ### END TODO


    def lip_max(self):
        """Computes the maximum of the lipschitz constants of f_i"""
        X, n_samples = self.X, self.n_samples
        ### TODO
        
        ### END TODO

## Checks for the logistic regression model


<div class="alert alert-block alert-warning">
    Check numerically the gradient using the function ``checkgrad`` from ``scipy.optimize`` (see below).
</div>

**Remark**: use the function `simu_logreg` to simulate data according to the logistic regression model

In [ ]:
## Simulation setting
n_features = 50
nnz = 20
idx = np.arange(n_features)
w0 = (-1) ** idx * np.exp(-idx / 10.)
w0[nnz:] = 0.

plt.figure(figsize=(5, 3))
plt.stem(w0, use_line_collection=True)
plt.title("Model weights")

In [ ]:
from scipy.optimize import check_grad

X, y = simu_logreg(w0, corr=0.6)
model = ModelLogReg(X, y)
w = np.random.randn(n_features)

print(check_grad(model.loss, model.grad, w)) # This must be a number (of order 1e-6)

In [ ]:
print("lip=", model.lip())
print("lip_max=", model.lip_max())

<a id='GD'></a>
## 3. Logistic regression on separable data via Gradient Descent

In [ ]:
def inspector(model, n_iter, verbose=True):
    """A closure called to update metrics after each iteration.
    Don't even look at it, we'll just use it in the solvers."""
    objectives = []
    it = [0] # This is a hack to be able to modify 'it' inside the closure.
    def inspector_cl(w):
        obj = model.loss(w)
        objectives.append(obj)
        if verbose == True:
            if it[0] == 0:
                print(' | '.join([name.center(8) for name in ["it", "obj"]]))
            if it[0] % (n_iter / 5) == 0:
                print(' | '.join([("%d" % it[0]).rjust(8), ("%.2e" % obj).rjust(8)]))
            it[0] += 1
    inspector_cl.objectives = objectives
    return inspector_cl

<a id='gd'></a>
## 3.1 Gradient descent

### QUESTIONS

<div class="alert alert-block alert-info">
1. Finish the function `gd` below that implements the gradient descent algorithm
- Test it using the next cell
</div>

In [ ]:
def gd(model, w0, n_iter, callback, verbose=True):
    """Gradient descent
    """
    step = 1 / model.lip()
    w = w0.copy()
    w_new = w0.copy()
    if verbose:
        print("Lauching GD solver...")
    callback(w)
    for k in range(n_iter + 1):
        ### TODO

        ### END TODO
        callback(w)
    return w

In [ ]:
n_iter =100
callback_gd = inspector(model, n_iter=n_iter)
w_gd = gd(model, w0, n_iter=n_iter, callback=callback_gd)

## 3.2 Data generation


<div class="alert alert-block alert-info">
    Generating *separable* data in 2D.
</div>

In [ ]:
#TO DO


#END TO DO
plt.scatter(X_sep[:, 0], X_sep[:, 1], c=Y_sep)
plt.scatter(mu1[0], mu1[1], color='k', s=100., alpha=0.8, marker='h')
plt.scatter(mu2[0], mu2[1], color='k', s=100., alpha=0.8, marker='h')
plt.axis('equal');

## 3.3 First iterations on the separable data


<div class="alert alert-block alert-info">
    Run 50 iterations of GD for the generated separable data.
</div>



In [ ]:
n_iter =50
model_sep = ModelLogReg(X_sep, Y_sep)
callback_gd_sep = inspector(model_sep, n_iter=n_iter)
beta_gd_sep = gd(model_sep, np.zeros(X_sep.shape[1]), n_iter=n_iter, callback=callback_gd_sep)

<div class="alert alert-block alert-info">
    Run an SVM for the generated separable data. 
    <br>
    <br>
    /!\ Beware of the management of the intercept.
</div>

In [ ]:
#TO DO

#END TO DO

<div class="alert alert-block alert-info">
    Plot the data and the obtained decision frontier. 
</div>

In [ ]:
#TO DO

#END TO DO

<div class="alert alert-block alert-info">
    Modify the gradient descent function to display the evolution of the decision frontier obtained via GD.
</div>

In [ ]:
def gd_sep_plot(model, w0, n_iter, callback, verbose=True):
    """Gradient descent with plots of decision frontier
    """
    X_sep = model.X
    Y_sep = model.y
    
    # Running an SVM
    # TO DO
    
    # END TO DO
    
    # Plot the data and the decision frontier
    # TO DO
    
    # END TO DO
    
    
    ax = plt.gca()
    
    
    step = 1 / model.lip()
    w = w0.copy()
    w_new = w0.copy()
    w_iter = np.zeros(())
  
    
    plt.plot(absc,ordo,color='k')
    if verbose:
        print("Lauching GD solver...")
    callback(w)
    for k in range(n_iter + 1):
        ### TODO

        ### END TODO
        callback(w)
        if (k%1000 == 0):
            plt.plot(absc, (-w[2]-w[0]*absc)/w[1])
    plt.savefig("fig1.pdf")
    plt.show()
    
    return w

In [ ]:
model_sep = ModelLogReg(X_sep, Y_sep)
n_iter = 20000
callback_gd_sep = inspector(model_sep, n_iter=n_iter)
beta_gd_sep = gd_sep_plot(model_sep, np.zeros(X_sep.shape[1]), n_iter=n_iter, callback=callback_gd_sep, verbose=False)

<a id='solvers'></a>
## 4. Other Solvers

We now have a class `ModelLogReg` that allows to compute $F(w)$, $\nabla F(w)$, 
$\nabla f_i(w)$ for the objective $F$
given by logistic regression.

We want now to code and compare several solvers to minimize $F$ in the case of separable data.

<a id='tools'></a>
## 4.1. Tools for the solvers

In [ ]:
# Starting point of all solvers
beta0 = np.zeros(model.n_features)

# Number of iterations
n_iter = 50

# Random samples indices for the stochastic solvers (sgd, sag, svrg)
idx_samples = np.random.randint(0, model.n_samples, model.n_samples * n_iter)

In [ ]:
def inspector(model, n_iter, verbose=True):
    """A closure called to update metrics after each iteration.
    Don't even look at it, we'll just use it in the solvers."""
    objectives = []
    it = [0] # This is a hack to be able to modify 'it' inside the closure.
    def inspector_cl(w):
        obj = model.loss(w)
        objectives.append(obj)
        if verbose == True:
            if it[0] == 0:
                print(' | '.join([name.center(8) for name in ["it", "obj"]]))
            if it[0] % (n_iter / 5) == 0:
                print(' | '.join([("%d" % it[0]).rjust(8), ("%.2e" % obj).rjust(8)]))
            it[0] += 1
    inspector_cl.objectives = objectives
    return inspector_cl

<a id='agd'></a>
## 4.3 Accelerated gradient descent

### QUESTIONS

<div class="alert alert-block alert-info">
    <ol>
        <li>Finish the function `agd` below that implements the accelerated gradient descent algorithm </li></br>
        <li> Test it using the next cell</li>
    </ol>
</div>

In [ ]:
def agd(model, w0, n_iter, callback, verbose=True):
    """Accelerated gradient descent
    """
    step = 1 / model.lip()
    w = w0.copy()
    w_new = w0.copy()
    # An extra variable is required for acceleration
    z = w0.copy()
    t = 1.
    t_new = 1.    
    if verbose:
        print("Lauching AGD solver...")
    callback(w)
    for k in range(n_iter + 1):
        ### TODO

        ### END TODO        
        callback(w)
    return w

In [ ]:
callback_agd = inspector(model, n_iter=n_iter)
w_agd = agd(model, w0, n_iter=n_iter, callback=callback_agd)

<a id='sgd'></a>
## 4.4 Stochastic gradient descent

### QUESTIONS

<div class="alert alert-block alert-info">
     <ol>
         <li> Finish the function `sgd` below that implements the st stochastic gradient descent algorithm </li>
         <li> Test it using the next cell </li>
    </ol>
</div> 
    

In [ ]:
def sgd(model, w0, idx_samples, n_iter, step, callback, verbose=True):
    """Stochastic gradient descent
    """
    w = w0.copy()
    callback(w)
    n_samples = model.n_samples
    for idx in range(n_iter):
        i = idx_samples[idx]
        ### TODO

        ### END TODO
        if idx % n_samples == 0:
            callback(w)
    return w

In [ ]:
step = 1e-1
callback_sgd = inspector(model, n_iter=n_iter)
w_sgd = sgd(model, w0, idx_samples, n_iter=model.n_samples * n_iter, 
            step=step, callback=callback_sgd)

<a id='sag'></a>
## 4.5. Stochastic average gradient descent


### QUESTIONS

<div class="alert alert-block alert-info">
    <ol>
        <li> Finish the function `sag` below that implements the stochastic averaged gradient algorithm </li>
        <li> Test it using the next cell </li>
    </ol>
</div>
    

In [ ]:
def sag(model, w0, idx_samples, n_iter, step, callback, verbose=True):
    """Stochastic average gradient descent
    """
    w = w0.copy()
    n_samples, n_features = model.n_samples, model.n_features
    gradient_memory = np.zeros((n_samples, n_features))
    y = np.zeros(n_features)
    callback(w)
    for idx in range(n_iter):
        i = idx_samples[idx]        
        ### TODO

        ### END OF TODO        
        if idx % n_samples == 0:
            callback(w)
    return w

In [ ]:
step = 1 / model.lip_max()
callback_sag = inspector(model, n_iter=n_iter)
w_sag = sag(model, w0, idx_samples, n_iter=model.n_samples * n_iter, 
            step=step, callback=callback_sag)

<a id='svrg'></a>
## 4.6. Stochastic variance reduced gradient

### QUESTIONS

<div class="alert alert-block alert-info">
    <ol> 
        <li>Finish the function `svrg` below that implements the stochastic variance reduced gradient algorithm </li>
        <li> Test it using the next cell </li>
    </ol>
</div>

In [ ]:
def svrg(model, w0, idx_samples, n_iter, step, callback, verbose=True):
    """Stochastic variance reduced gradient descent
    """
    w = w0.copy()
    w_old = w.copy()
    n_samples = model.n_samples
    callback(w)
    for idx in range(n_iter):        
        ### TODO

        ### END TODO        
        if idx % n_samples == 0:
            callback(w)
    return 

In [ ]:
step = 1 / model.lip_max()
callback_svrg = inspector(model, n_iter=n_iter)
w_svrg = svrg(model, w0, idx_samples, n_iter=model.n_samples * n_iter,
              step=step, callback=callback_svrg)